-sandbox

# Delta Lake: Turn your Data Lake into a Lakehouse
&nbsp;
&nbsp;
<div style="background:#110336">
  <img src="https://dataengconf.com.au//images/dataEngLogos/DataEng.MeetUp600x450.option1.v1.jpg?w=320&q=75" style="height:200px"/>
  <img src="https://delta.io/static/delta-lake-logo-a1c0d80d23c17de5f5d7224cb40f15dc.svg" style="height:100px; padding:50px 0;"/>
</div>
&nbsp;

This notebook was prepared for [my talk](https://dataengconf.com.au/conference/schedule) at the [**DataEngBytes** conference](https://dataengconf.com.au/conference/sydney) held on 2022-09-29 in Sydney, Australia.    

- Author: Vinoaj (Vinny) Vijeyakumaar (vinoaj@gmail.com, vinny.vijeyakumaar@databricks.com)
- _Opinions are my own and not necessarily the views of my employer_


## Demo Objectives

Delta Lake provides ACID transactions, scalable metadata handling, and unifies streaming and batch data processing on top of existing data lakes. 

In this demo, we will touch upon Delta Lake's more powerful features:
* ACID transactions
* DML support
* Unify batch & streaming
* Time Travel
* Zero copy clones
* Change data feeds
* ... and more!


### The Data

The data used in this demo is from the Kaggle competition [`predict-closed-questions-on-stack-overflow`](https://www.kaggle.com/competitions/predict-closed-questions-on-stack-overflow/overview).


### The Environment
This notebooks is setup to run in a Databricks Workspace. Databricks clusters are already set up with Spark, Delta Lake, and their respective SDKs (e.g. PySpark). This notebook was developed using **DBR 11.2** (_Spark 3.3.0_)

To set up Delta Lake in a non-Databricks environment, please [follow these instructions](https://docs.delta.io/latest/quick-start.html)

## Environment setup

In [0]:
!pip install kaggle

     |████████████████████████████████| 58 kB 3.1 MB/s 
     |████████████████████████████████| 78 kB 4.1 MB/s 
     |████████████████████████████████| 78 kB 5.2 MB/s 
  Created wheel for kaggle: filename=kaggle-1.5.12-py3-none-any.whl size=73051 sha256=96086b4db360f9af71cbb91d250c16e5987624591e9d13b7f9a9d760a646f271
  Stored in directory: /root/.cache/pip/wheels/ac/b2/c3/fa4706d469b5879105991d1c8be9a3c2ef329ba9fe2ce5085e
Successfully built kaggle
You should consider upgrading via the '/local_disk0/.ephemeral_nfs/envs/pythonEnv-15babe31-d3b7-4077-9b1c-a808cf85bcb7/bin/python -m pip install --upgrade pip' command.


In [0]:
import json
import os

We assume API credentials have already been stored in [Databricks Secrets](https://docs.databricks.com/security/secrets/index.html).

In [0]:
USERNAME = "vinny.vijeyakumaar@databricks.com"
SECRETS_SCOPE = "vinnyvijeyakumaar"

KAGGLE_USERNAME = dbutils.secrets.get(scope=SECRETS_SCOPE, key="KAGGLE_USERNAME")
KAGGLE_KEY = dbutils.secrets.get(scope=SECRETS_SCOPE, key="KAGGLE_KEY")
KAGGLE_COMPETITION = "predict-closed-questions-on-stack-overflow"

TABLE_NAME = "stackoverflow_train01"

os.environ['USERNAME'] = USERNAME
os.environ['KAGGLE_USERNAME'] = KAGGLE_USERNAME
os.environ['KAGGLE_KEY'] = KAGGLE_KEY
os.environ['KAGGLE_COMPETITION'] = KAGGLE_COMPETITION

import kaggle

In [0]:
dbutils.fs.mkdirs(f"/Users/{USERNAME}/custom_demos/input_files/")
dbutils.fs.mkdirs(f"/Users/{USERNAME}/custom_demos/lakehouse/{KAGGLE_COMPETITION}")

# Start with a clean slate by cleaning up artifacts from previous demo runs
dbutils.fs.rm(f"/Users/{USERNAME}/custom_demos/lakehouse/{KAGGLE_COMPETITION}/{TABLE_NAME}", True)

display(dbutils.fs.ls(f"/Users/{USERNAME}/custom_demos/"))

path name size modificationTime dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/input_files/ input_files/ 0 1664312743609 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/ lakehouse/ 0 1664312743609

In [0]:
print(f"/Users/{USERNAME}/custom_demos/lakehouse/{KAGGLE_COMPETITION}/{TABLE_NAME}")
dbutils.fs.rm(f"/Users/{USERNAME}/custom_demos/lakehouse/{KAGGLE_COMPETITION}/{TABLE_NAME}", True)

/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01
Out[22]: False

### Download and prepare data files from Kaggle
[Kaggle API documentation](https://github.com/Kaggle/kaggle-api)

In [0]:
!kaggle competitions download -c $KAGGLE_COMPETITION -p /tmp/$USERNAME/

 18%|██████▊                  

*** WARNING: max output size exceeded, skipping output. ***

100%|█████████████████████████████████████▉| 14.9G/15.0G [04:12<00:00, 49.4MB/s]
100%|██████████████████████████████████████| 15.0G/15.0G [04:12<00:00, 63.6MB/s]


In [0]:
%sh
# Create output directory
mkdir -p /tmp/$USERNAME/files/$KAGGLE_COMPETITION/

# Extract files
unzip /tmp/$USERNAME/$KAGGLE_COMPETITION.zip -d /tmp/$USERNAME/files/$KAGGLE_COMPETITION/

Archive:  /tmp/vinny.vijeyakumaar@databricks.com/predict-closed-questions-on-stack-overflow.zip
  inflating: /tmp/vinny.vijeyakumaar@databricks.com/files/predict-closed-questions-on-stack-overflow/2012-07 Stack Overflow.7z  
  inflating: /tmp/vinny.vijeyakumaar@databricks.com/files/predict-closed-questions-on-stack-overflow/basic_benchmark.csv  
  inflating: /tmp/vinny.vijeyakumaar@databricks.com/files/predict-closed-questions-on-stack-overflow/prior_benchmark.csv  
  inflating: /tmp/vinny.vijeyakumaar@databricks.com/files/predict-closed-questions-on-stack-overflow/private leaderboard raw.7z  
  inflating: /tmp/vinny.vijeyakumaar@databricks.com/files/predict-closed-questions-on-stack-overflow/private_leaderboard.7z  
  inflating: /tmp/vinny.vijeyakumaar@databricks.com/files/predict-closed-questions-on-stack-overflow/private_leaderboard.csv  
  inflating: /tmp/vinny.vijeyakumaar@databricks.com/files/predict-closed-questions-on-stack-overflow/private_leaderboard.gz  
  inflating: /tmp/vi

In [0]:
#cleanup
!rm /tmp/$USERNAME/$KAGGLE_COMPETITION.zip

In [0]:
!ls -la /tmp/$USERNAME/files/$KAGGLE_COMPETITION/

total 20971152
drwxr-xr-x 2 root root       4096 Sep 27 20:53  .
drwxr-xr-x 3 root root       4096 Sep 27 20:48  ..
-rw-r--r-- 1 root root 6653184708 Dec 12  2019 '2012-07 Stack Overflow.7z'
-rw-r--r-- 1 root root    7952326 Dec 12  2019  basic_benchmark.csv
-rw-r--r-- 1 root root    7842030 Dec 12  2019  prior_benchmark.csv
-rw-r--r-- 1 root root   24591887 Dec 12  2019 'private leaderboard raw.7z'
-rw-r--r-- 1 root root   24517377 Dec 12  2019  private_leaderboard.7z
-rw-r--r-- 1 root root  104510048 Dec 12  2019  private_leaderboard.csv
-rw-r--r-- 1 root root   34520679 Dec 12  2019  private_leaderboard.gz
-rw-r--r-- 1 root root   36069107 Dec 12  2019  private_leaderboard.zip
-rw-r--r-- 1 root root   21788714 Dec 12  2019  public_leaderboard.7z
-rw-r--r-- 1 root root   92388506 Dec 12  2019  public_leaderboard.csv
-rw-r--r-- 1 root root   30784595 Dec 12  2019  public_leaderboard.gz
-rw-r--r-- 1 root root   16777216 Dec 12  2019  public_leaderboard.zip
-rw-r--r-- 1 root root     81

In [0]:
!head /tmp/$USERNAME/files/$KAGGLE_COMPETITION/train.csv

The downloaded and unzipped files are stored on the driver's local disk. 
We now move the relevant files to `DBFS` so that they're persisted on cloud storage.

For the purposes of this demo, we'll only move `train.csv`

In [0]:
file_pattern = "train.csv"

dbutils.fs.cp(f"file:/tmp/{USERNAME}/files/{KAGGLE_COMPETITION}/{file_pattern}", 
              f"/Users/{USERNAME}/custom_demos/input_files/{KAGGLE_COMPETITION}/", 
              True)

Out[9]: True

In [0]:
display(dbutils.fs.ls(f"/Users/{USERNAME}/custom_demos/input_files/{KAGGLE_COMPETITION}/"))

path name size modificationTime dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/input_files/predict-closed-questions-on-stack-overflow/train.csv train.csv 3729150126 1664312005000

In [0]:
#cleanup
!rm -rf /tmp/$USERNAME/files/$KAGGLE_COMPETITION/

## ![](https://pages.databricks.com/rs/094-YMS-629/images/delta-lake-tiny-logo.png) Delta introduction

### ![](https://pages.databricks.com/rs/094-YMS-629/images/delta-lake-tiny-logo.png) Import Data and create a Delta Lake Table

&nbsp;

<img src="https://databricks.com/wp-content/uploads/2020/12/simplysaydelta.png" width=600/>

### Delta Table creation with PySpark

In [0]:
filename = "train.csv"
filepath = f"/Users/{USERNAME}/custom_demos/input_files/{KAGGLE_COMPETITION}/{filename}"
print(f"Loading contents of: {filepath}")

data_csv = (spark.read
                 .option("header", "true")
                 .option("multiLine", "true")
                 .option("escape", '"') # Handle double quotes in multiline entries
                 .csv(filepath))

(data_csv.write
   .format("delta")
   .mode("overwrite")
   # All Delta Lake files (i.e. data and log files) for this table will be stored here
   .save(f"/Users/{USERNAME}/custom_demos/lakehouse/stackoverflow_train00"))

Loading contents of: /Users/vinny.vijeyakumaar@databricks.com/custom_demos/input_files/predict-closed-questions-on-stack-overflow/train.csv


In [0]:
(spark.read.format("delta")
   .load(f"/Users/{USERNAME}/custom_demos/lakehouse/stackoverflow_train00")
   .display())

PostId PostCreationDate OwnerUserId OwnerCreationDate ReputationAtPostCreation OwnerUndeletedAnswerCountAtPostTime Title BodyMarkdown Tag1 Tag2 Tag3 Tag4 Tag5 PostClosedDate OpenStatus 5962349 05/11/2011 09:52:09 328725 04/29/2010 09:48:48 937 59 Problems with deployment, advice needed for a web-based java application I have developed a command-line (read: no GUI) Java application which crunches through numbers based on a given dataset and a series of parameters; and spits out a series of HTML files as resultant reports. These reports hold a large amount of data in tables, so in order to give the users a easy and quick overview of the results, I utilized the JUNG2 library and created a nice graph. 

Here's where it gets interesting; since I would like the graph to be interactive it should be deployed after the application has run and files are generated, whenever the user wants to view the reports. I decided to go with an applet based deployment, however I am not too happy with the current setup due to the following reasons:

 1. I want to make the software as simple to use as possible (my users won't be tech-savvy, and even tech-intimidated in most cases). I would really like to distribute one JAR only, which forced me to put the applet with everything else it needs in a package in the same JAR as the main application.

 2. The applet and the main application need to communicate the results, so I create a xML-based report which is used to hold information. As long as the files are on a local machine and are not moved around it all works fine. Unfortunately I also need the files to be moved around. A user should be able to take the "results" folder to a USB stick, go anywhere plug the stick to another computer and be able to use the report as he/she likes.

For the time being the applets are implemented with the following html code:

 
 
 

As you can see this applet will not work if the parent folder is moved to another location.

----------------
As far as I know I have a couple of alternatives: 

 a) Change codebase to point to an URL on our webserver where I could put the jar file. This however creates the problem with permissions, as the applet will not be able to read the results file. Alternative is to upload the results file to the server when the user wants to visualize the graph, although I am not sure if that's a good option due to server security and also if it could be made so that upload happens automatically without bothering the user.

b) I can use a relative path on the codebase attribute, but then the whole folder hierarchy needs to be intact upon copy. This could be a last resort, if I cant come up with a better way to do it.

c) change the deployment method (would like to avoid this alternative to not spend more time on the development phase)

Any ideas? Am I missing something? How could I tackle this problem?
Thanks, java applet null null null null open 5962351 05/11/2011 09:52:22 710997 04/16/2011 08:58:46 3 0 Retrieve the url of an image taken on the fly and saved in the gallery, how? I allow the user to choose an image from the gallery or take a photo with the camera.
I would to save the image path in both cases so that I can use it to display the image in a second moment.

When the user select an image from the gallery, I can use


 - (void)imagePickerController:(UIImagePickerController *)picker didFinishPickingMediaWithInfo:(NSDictionary *)info {

	
 if([[info valueForKey:@"UIImagePickerControllerMediaType"] isEqualToString:@"public.image"]) {
 NSURL *imageUrl = [info valueForKey:@"UIImagePickerControllerReferenceURL"];
 
	}
}

Instead, if the user takes a photo on the fly, I save it in the photo roll with:

 UIImage *image = [info objectForKey:@"UIImagePickerControllerOriginalImage"];
 
 UIImageWriteToSavedPhotosAlbum(image, self, @selector(image:didFinishSavingWithError:contextInfo:), nil);


After saving it, I would to retrieve the corresponding NSURL as the user had selected it.

How could I do?
 

### Delta Table creation using SQL

Let's do the same with SQL instead


- First use Databricks' native handling of CSVs to create a temporary view with the CSV data
- Then create a Delta Table, specifying
  - Partition columns
  - Table properties (note: `autoOptimize` features are prioritised in Delta Lake's [current roadmap](https://github.com/delta-io/delta/issues/1307))
  - Location to host the Delta data and log files

In [0]:
%sql
CREATE OR REPLACE TEMPORARY VIEW tvw_train
USING CSV -- Databricks-specific operator
OPTIONS(
  path "/Users/vinny.vijeyakumaar@databricks.com/custom_demos/input_files/predict-closed-questions-on-stack-overflow/train.csv",
  header "true", multiLine "true", escape '"'
);

-- DROP TABLE IF EXISTS vinny_vijeyakumaar.stackoverflow_train01;

-- Create the Delta table
CREATE OR REPLACE TABLE vinny_vijeyakumaar.stackoverflow_train01
USING DELTA
PARTITIONED BY (PostCreationDate)
TBLPROPERTIES(
  delta.enableChangeDataFeed = true, 
  -- autoOptimize.* currently available in Databricks; P1 priority on current Delta Lake OSS roadmap
  delta.autoOptimize.optimizeWrite = true, 
  delta.autoOptimize.autoCompact = true
)
-- (Optional) All Delta Lake files (i.e. data and log files) for this table will be stored here
-- If not specified, location will be managed by your active metastore
LOCATION "/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01"
AS
  SELECT 
    PostId
    , DATE(TO_TIMESTAMP(PostCreationDate, "MM/dd/yyyy HH:mm:ss")) AS PostCreationDate
    , * EXCEPT (PostId, PostCreationDate)
  FROM tvw_train;

-- Cleanup
DROP VIEW IF EXISTS tvw_train;

-- Show data
SELECT *
FROM vinny_vijeyakumaar.stackoverflow_train01;

PostId PostCreationDate OwnerUserId OwnerCreationDate ReputationAtPostCreation OwnerUndeletedAnswerCountAtPostTime Title BodyMarkdown Tag1 Tag2 Tag3 Tag4 Tag5 PostClosedDate OpenStatus 8704 2008-08-12 1042 08/11/2008 18:02:48 1 0 Final managed exception handler in a mixed native/managed executable? I have an MFC application compiled with /clr and I'm trying to implement a final handler for otherwise un-caught managed exceptions. For native exceptions, overriding CWinApp::ProcessWndProcException works.

The two events suggested in Jeff's CodeProject article, Application.ThreadException and AppDomain.CurrentDomain.UnhandledException, are not raised.

Can anyone suggest a way to provide a final managed exception handler for a mixed executable? unhandled exception mixed executable null null open 8702 2008-08-12 1097 08/12/2008 11:40:09 1 0 What is the IDE for classic ASP and VBScript? Yes, I'm stuck supporting a legacy ASP application. I currently have VS2008 installed but it complains incessantly about the ASP and VBScript I am dealing with. What would be a better IDE to use to make it less sucky?

Thanks,

Geoff ide asp vbscript null null null open 9009 2008-08-12 238 08/03/2008 21:42:37 94 13 Perl conditional operator is giving the wrong result This snippet of perl code in my program is giving the wrong result.

 $condition ? $a= 2 : $a= 3 ;
 print $a;

No matter what the value of $condition is, the output is always 3, how come?

 perl conditional operator null null null open 8728 2008-08-12 1008 08/11/2008 12:53:05 21 2 Delphi MDI Application and the titlebar of the MDI Children I've got an MDI application written in Delphi 2006 which runs XP with the default theme. Is there a way of controlling the appearance of the MDI Children to avoid the large XP-style title bar on each window? I've tried setting the BorderStyle of the MDIChildren to bsSizeToolWin but they are still rendered as normal Forms. delphi forms mdi null null null open 8726 2008-08-12 572 08/06/2008 20:56:54 115 11 Checking FTP status codes with a PHP script. I have a script that checks responses from HTTP servers using the PEAR HTTP classes. However, I've recently found that the script fails on FTP servers (and probably anything that's not HTTP or HTTPS). I tried Google, but didn't see any scripts or code that returned the server status code from servers other than HTTP servers.

How can I find out the status of a newsgroup or FTP server using PHP?

Please note that, although most of the time I'm language agnostic, the entire website is PHP-driven, so a PHP solution would be the best for easy of maintainability and extensibility in the future. php http ftp server-response pear null open 8493 2008-08-12 459 08/05/2008 21:54:42 11 4 What's in your .procmailrc Are there any handy general items you put in your .procmailrc file? unix email procmail .procmailrc null 09/09/2011 15:08:40 not constructive 8987 2008-08-12 940 08/10/2008 19:58:38 48 4 Calling Table-Valued SQL Functions From .NET Scalar-valued functions can be called from .NET as follows:

 SqlCommand cmd = new SqlCommand("testFunction", sqlConn); //testFunction is scalar
 cmd.CommandType = CommandType.StoredProcedure; 
 cmd.Parameters.Add("retVal", SqlDbType.Int);
 cmd.Parameters["retVal"].Direction = ParameterDirection.ReturnValue;
 cmd.ExecuteScalar();
 int aFunctionResult = (int)cmd.Parameters["retVal"].Value;


I also know that table-valued functions can be called in a similar fashion, for example: 

 String query = "select * from testFunction(param1,...)"; //testFunction is table-valued
 SqlCommand cmd = new SqlCommand(query, sqlConn);
 SqlDataAdapter adapter = new SqlDataAdapter(cmd);
 adapter.Fill(tbl);


My question is, can table-valued functions be called as stored procedures, like scalar-valued functions can? (e.g., replicate my first code snippet with a table-valued function being called and getting the returned table through a ReturnValue parameter). c# .net sql null null null open 8612 2008-08

## ![](https://pages.databricks.com/rs/094-YMS-629/images/delta-lake-tiny-logo.png) Exploring Delta Lake's file structure

In [0]:
%sql 
DESCRIBE DETAIL vinny_vijeyakumaar.stackoverflow_train01;

format id name description location createdAt lastModified partitionColumns numFiles sizeInBytes properties minReaderVersion minWriterVersion delta 4559acb4-b52e-4c6b-9f8f-adc8cf079802 vinny_vijeyakumaar.stackoverflow_train01 null dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01 2022-09-27T21:07:09.399+0000 2022-09-27T21:13:50.000+0000 List(PostCreationDate) 1462 1972415159 Map(delta.enableChangeDataFeed -> true, delta.autoOptimize.autoCompact -> true, delta.autoOptimize.optimizeWrite -> true) 1 4

In [0]:
%sql
DESCRIBE HISTORY vinny_vijeyakumaar.stackoverflow_train01
LIMIT 10;

version timestamp userId userName operation operationParameters job notebook clusterId readVersion isolationLevel isBlindAppend operationMetrics userMetadata engineInfo 0 2022-09-27T21:13:50.000+0000 5211215277230706 vinny.vijeyakumaar@databricks.com CREATE OR REPLACE TABLE AS SELECT Map(isManaged -> false, description -> null, partitionBy -> ["PostCreationDate"], properties -> {"delta.enableChangeDataFeed":"true","delta.autoOptimize.autoCompact":"true","delta.autoOptimize.optimizeWrite":"true"}) null List(3008062229322400) 0923-094955-git4n0b4 null WriteSerializable false Map(numFiles -> 1462, numOutputRows -> 3370528, numOutputBytes -> 1972415159) null Databricks-Runtime/11.2.x-photon-scala2.12

In [0]:
# Move paths to variables for easier readability
delta_lake_dbfs_path = f"/Users/{USERNAME}/custom_demos/lakehouse/{KAGGLE_COMPETITION}/stackoverflow_train01/"
delta_lake_dir = f"/dbfs{delta_lake_dbfs_path}"
os.environ['DL_DIR'] = delta_lake_dir

print(f"DBFS path: {delta_lake_dbfs_path}")
print(f"File IO path: {delta_lake_dir}")

def display_log_files(path=None):
  if path is None:
    path = f"{delta_lake_dbfs_path}/_delta_log/"
  
  print(f"Displaying contents of {path}")
  display(dbutils.fs.ls(path))

DBFS path: /Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/
File IO path: /dbfs/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/


### Data Files
- Data is stored in standard `.parquet` files in the top level directory for the data
- As expected, partitions sit in their own subdirectories

In [0]:
path = f"{delta_lake_dbfs_path}PostCreationDate=2008-07-31/"
print(f"Displaying contents of {path}")
display(dbutils.fs.ls(path))

Displaying contents of /Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/PostCreationDate=2008-07-31/


path name size modificationTime dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/PostCreationDate=2008-07-31/part-00000-d406e64b-d96d-4ffc-a436-dda8b0a6b16f.c000.snappy.parquet part-00000-d406e64b-d96d-4ffc-a436-dda8b0a6b16f.c000.snappy.parquet 5614 1664312907000

### Log files
- Transaction log files are stored at the top level `_delta_log/` directory 
- A `.json` log file is created at the end of every successful transaction
- A checkpoint log is created every `n` transactions, and is stored in the `_last_checkpoint` directory

_Note_: even

In [0]:
path = f"{delta_lake_dbfs_path}_delta_log/"
print(f"Displaying contents of {path}")
display(dbutils.fs.ls(path))

Displaying contents of /Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/


path name size modificationTime dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/.s3-optimization-0 .s3-optimization-0 0 1664313233000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/.s3-optimization-1 .s3-optimization-1 0 1664313233000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/.s3-optimization-2 .s3-optimization-2 0 1664313233000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000000.crc 00000000000000000000.crc 3213 1664313233000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000000.json 00000000000000000000.json 2444853 1664313230000

In [0]:
!head $DL_DIR/_delta_log/00000000000000000000.json

{"protocol":{"minReaderVersion":1,"minWriterVersion":4}}
{"metaData":{"id":"4559acb4-b52e-4c6b-9f8f-adc8cf079802","format":{"provider":"parquet","options":{}},"schemaString":"{\"type\":\"struct\",\"fields\":[{\"name\":\"PostId\",\"type\":\"string\",\"nullable\":true,\"metadata\":{}},{\"name\":\"PostCreationDate\",\"type\":\"date\",\"nullable\":true,\"metadata\":{}},{\"name\":\"OwnerUserId\",\"type\":\"string\",\"nullable\":true,\"metadata\":{}},{\"name\":\"OwnerCreationDate\",\"type\":\"string\",\"nullable\":true,\"metadata\":{}},{\"name\":\"ReputationAtPostCreation\",\"type\":\"string\",\"nullable\":true,\"metadata\":{}},{\"name\":\"OwnerUndeletedAnswerCountAtPostTime\",\"type\":\"string\",\"nullable\":true,\"metadata\":{}},{\"name\":\"Title\",\"type\":\"string\",\"nullable\":true,\"metadata\":{}},{\"name\":\"BodyMarkdown\",\"type\":\"string\",\"nullable\":true,\"metadata\":{}},{\"name\":\"Tag1\",\"type\":\"string\",\"nullable\":true,\"metadata\":{}},{\"name\":\"Tag2\",\"type\":\"stri

In [0]:
# Since it's a JSONL file, we'll parse it line-by-line
def pretty_print_log(filename:str):
  if filename.startswith("/dbfs/") is False:
    filename = "/dbfs" + filename
  
  with open(filename, "r") as logfile:
    for line in logfile:
      print(json.dumps(json.loads(line), indent=4))


log_path = f"{delta_lake_dir}/_delta_log/00000000000000000000.json"
pretty_print_log(log_path)

{
    "protocol": {
        "minReaderVersion": 1,
        "minWriterVersion": 4
    }
}
{
    "metaData": {
        "id": "4559acb4-b52e-4c6b-9f8f-adc8cf079802",
        "format": {
            "provider": "parquet",
            "options": {}
        },
        "schemaString": "{\"type\":\"struct\",\"fields\":[{\"name\":\"PostId\",\"type\":\"string\",\"nullable\":true,\"metadata\":{}},{\"name\":\"PostCreationDate\",\"type\":\"date\",\"nullable\":true,\"metadata\":{}},{\"name\":\"OwnerUserId\",\"type\":\"string\",\"nullable\":true,\"metadata\":{}},{\"name\":\"OwnerCreationDate\",\"type\":\"string\",\"nullable\":true,\"metadata\":{}},{\"name\":\"ReputationAtPostCreation\",\"type\":\"string\",\"nullable\":true,\"metadata\":{}},{\"name\":\"OwnerUndeletedAnswerCountAtPostTime\",\"type\":\"string\",\"nullable\":true,\"metadata\":{}},{\"name\":\"Title\",\"type\":\"string\",\"nullable\":true,\"metadata\":{}},{\"name\":\"BodyMarkdown\",\"type\":\"string\",\"nullable\":true,\"metadata\":{}},{\"

In [0]:
# Let's get a clean view of some of the stats (look for the first "add" entry with stats)

with open(log_path, "r") as logfile:
  for line in logfile: 
    try:
      json_obj = json.loads(line)
      stats = json_obj["add"]["stats"]
      print(f"File: {json_obj['add']['path']}")
      json_stats = json.loads(stats)
      print(json.dumps(json_stats, indent=4))
      break
    except (KeyError, IndexError):
      pass
      

File: PostCreationDate=2008-07-31/part-00000-d406e64b-d96d-4ffc-a436-dda8b0a6b16f.c000.snappy.parquet
{
    "numRecords": 5,
    "minValues": {
        "PostId": "11",
        "OwnerUserId": "1",
        "OwnerCreationDate": "07/31/2008 14:22:31",
        "ReputationAtPostCreation": "1",
        "OwnerUndeletedAnswerCountAtPostTime": "0",
        "Title": "Decimal vs Double?",
        "BodyMarkdown": "Are there any conversion tools f",
        "Tag1": "c#",
        "Tag2": "css",
        "OpenStatus": "open"
    },
    "maxValues": {
        "PostId": "9",
        "OwnerUserId": "9",
        "OwnerCreationDate": "07/31/2008 21:35:26",
        "ReputationAtPostCreation": "16",
        "OwnerUndeletedAnswerCountAtPostTime": "2",
        "Title": "Tools for porting J# code to C#",
        "BodyMarkdown": "I've got an absolutely positione\ufffd",
        "Tag1": "j#",
        "Tag2": "css",
        "OpenStatus": "open"
    },
    "nullCount": {
        "PostId": 0,
        "OwnerUserId": 0

## ![](https://pages.databricks.com/rs/094-YMS-629/images/delta-lake-tiny-logo.png) Unified Batch and Streaming Source and Sink

These cells showcase streaming and batch concurrent queries (inserts and reads)
* We will run a streaming query on this data
* This notebook will run an `INSERT` against our `lending_club_delta` table

In [0]:
# Read the insertion of data
(spark.readStream
   .table("vinny_vijeyakumaar.stackoverflow_train")
   .createOrReplaceTempView("vv_so_train_readStream"))

In [0]:
%sql
-- Let's look up a user who shouldn't yet exist
SELECT *
FROM vv_so_train_readStream
WHERE OwnerUserId = 999999999

**Wait** until the stream is up and running before executing the code below

In [0]:
%sql 
insert into vinny_vijeyakumaar.stackoverflow_train (sk, OwnerUserId) 
    values (999999999, 999999999) 

##![](https://pages.databricks.com/rs/094-YMS-629/images/delta-lake-tiny-logo.png) Full DML Support

Delta Lake supports standard DML including UPDATE, DELETE and MERGE INTO providing developers more controls to manage their big datasets.

### Delete rows

In [0]:
%sql
-- Remove "off topic" posts
DELETE FROM vinny_vijeyakumaar.stackoverflow_train01 
WHERE OpenStatus = 'off topic'

num_affected_rows 17530

### Update rows

In [0]:
%sql
-- Capitalise "open" values
UPDATE vinny_vijeyakumaar.stackoverflow_train01 
SET OpenStatus = "OPEN" 
WHERE OpenStatus = "open"

num_affected_rows 3300392

In [0]:
display_log_files()

Displaying contents of /Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01//_delta_log/


path name size modificationTime dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/.s3-optimization-0 .s3-optimization-0 0 1664313233000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/.s3-optimization-1 .s3-optimization-1 0 1664313233000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/.s3-optimization-2 .s3-optimization-2 0 1664313233000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000000.crc 00000000000000000000.crc 3213 1664313233000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000000.json 00000000000000000000.json 2444853 1664313230000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000001.crc 00000000000000000001.crc 3213 1664313687000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000001.json 00000000000000000001.json 3211640 1664313685000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000002.checkpoint.parquet 00000000000000000002.checkpoint.parquet 1141119 1664313819000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000002.crc 00000000000000000002.crc 3212 1664313815000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000002.json 00000000000000000002.json 3391011 1664313813000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/_last_checkpoint _last_checkpoint 6853 1664313819000

### MERGE INTO
Upsert into tables using the [`MERGE` SQL Operation](https://docs.delta.io/latest/delta-update.html#upsert-into-a-table-using-merge). 

In non-Databricks environments, see [Configure SparkSession](https://docs.delta.io/latest/delta-batch.html#-sql-support) for steps to enable support for SQL commands.

Let's create a table `load_updates` that contains new data from a source data store

In [0]:
%sql
-- DROP TABLE vinny_vijeyakumaar.load_updates;

CREATE TABLE IF NOT EXISTS vinny_vijeyakumaar.load_updates (
  PostId string, PostCreationDate string, OwnerUserId string,
  OwnerCreationDate string, ReputationAtPostCreation string,
  OwnerUndeletedAnswerCountAtPostTime string, Title string, BodyMarkdown string,
  Tag1 string, Tag2 string, Tag3 string, Tag4 string, Tag5 string, PostClosedDate string,
  OpenStatus string
);

TRUNCATE TABLE vinny_vijeyakumaar.load_updates;

INSERT INTO vinny_vijeyakumaar.load_updates VALUES
  (999999, DATE("2007-08-01"), "", 999999, "", "", "", "", "", "", "", "", "", "", ""),
  (888888, DATE("2007-08-01"), "", 888888, "", "", "", "", "", "", "", "", "", "", ""),
  (1167904, DATE("2007-08-01"), "", 1167904, "", "", "", "", "", "", "", "", "", "", ""),
  (1078360, DATE("2007-08-01"), "", 1078360, "", "", "", "", "", "", "", "", "", "", "");

SELECT * FROM vinny_vijeyakumaar.load_updates;

PostId PostCreationDate OwnerUserId OwnerCreationDate ReputationAtPostCreation OwnerUndeletedAnswerCountAtPostTime Title BodyMarkdown Tag1 Tag2 Tag3 Tag4 Tag5 PostClosedDate OpenStatus 1167904 2007-08-01 1167904 1078360 2007-08-01 1078360 888888 2007-08-01 888888 999999 2007-08-01 999999

In [0]:
%sql
MERGE INTO vinny_vijeyakumaar.stackoverflow_train01 AS target
USING vinny_vijeyakumaar.load_updates AS source
ON target.PostId = source.PostId
WHEN MATCHED THEN 
  UPDATE SET * -- Update all columns
WHEN NOT MATCHED 
  THEN INSERT *;
  
SELECT * FROM vinny_vijeyakumaar.stackoverflow_train01 WHERE PostId IN (999999, 888888, 1167904, 1078360);

PostId PostCreationDate OwnerUserId OwnerCreationDate ReputationAtPostCreation OwnerUndeletedAnswerCountAtPostTime Title BodyMarkdown Tag1 Tag2 Tag3 Tag4 Tag5 PostClosedDate OpenStatus 888888 2007-08-01 888888 1078360 2007-08-01 1078360 999999 2007-08-01 999999 1167904 2007-08-01 1167904

In [0]:
display_log_files()

Displaying contents of /Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01//_delta_log/


path name size modificationTime dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/.s3-optimization-0 .s3-optimization-0 0 1664313233000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/.s3-optimization-1 .s3-optimization-1 0 1664313233000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/.s3-optimization-2 .s3-optimization-2 0 1664313233000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000000.crc 00000000000000000000.crc 3213 1664313233000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000000.json 00000000000000000000.json 2444853 1664313230000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000001.crc 00000000000000000001.crc 3213 1664313687000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000001.json 00000000000000000001.json 3211640 1664313685000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000002.checkpoint.parquet 00000000000000000002.checkpoint.parquet 1141119 1664313819000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000002.crc 00000000000000000002.crc 3212 1664313815000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000002.json 00000000000000000002.json 3391011 1664313813000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000003.crc 00000000000000000003.crc 3212 1664313926000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000003.json 00000000000000000003.json 2248 1664313922000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000004.crc 00000000000000000004.crc 3212 1664313994000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000004.json 00000000000000000004.json 896 1664313993000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000005.crc 00000000000000000005.crc 3213 1664314025000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000005.json 00000000000000000005.json 2231 1664314022000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000006.crc 00000000000000000006.crc 3213 1664314052000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000006.json 00000000000000000006.json 2882 1664314050000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-ove

In [0]:
log_path = f"{delta_lake_dir}/_delta_log/00000000000000000006.json"
pretty_print_log(log_path)

{
    "remove": {
        "path": "PostCreationDate=2007-08-01/part-00000-f982e89f-4264-43bb-a043-f1ba0a27492c.c000.snappy.parquet",
        "deletionTimestamp": 1664314049556,
        "dataChange": true,
        "extendedFileMetadata": true,
        "partitionValues": {
            "PostCreationDate": "2007-08-01"
        },
        "size": 3376,
        "tags": {
            "INSERTION_TIME": "1664314022000000",
            "MIN_INSERTION_TIME": "1664314022000000",
            "MAX_INSERTION_TIME": "1664314022000000",
            "OPTIMIZE_TARGET_SIZE": "268435456"
        }
    }
}
{
    "add": {
        "path": "PostCreationDate=2007-08-01/part-00000-5d440efc-3877-4fa4-8486-6725dc987151.c000.snappy.parquet",
        "partitionValues": {
            "PostCreationDate": "2007-08-01"
        },
        "size": 3550,
        "modificationTime": 1664314050000,
        "dataChange": true,
        "stats": "{\"numRecords\":4,\"minValues\":{\"PostId\":\"1078360\",\"OwnerUserId\":\"\",\"Own

## Checkpoint files

-sandbox
<img src="https://github.com/QuentinAmbard/databricks-demo/raw/main/retail/resources/images/delta-lake-perf-bench.png" width="500" style="float: right; margin-left: 50px"/>

### Blazing fast query at scale

Log files are compacted in a parquet checkpoint every `n` commits. The checkpoint file contains the entire table structure.

Table is self suficient, the metastore doesn't store additional information removing bottleneck and scaling metadata

This result in **fast read query**, even with a growing number of files/partitions!

### Let's generate more transaction logs

In [0]:
import random

def generate_transactions(n_transactions:int=1):
  for _ in range(n_transactions):
    scenario = random.randrange(0,2,1)
    
    if scenario == 0:
      # print(f"Scenario {scenario}")
      [x, y] = random.sample(range(100000,999999), 2)
      spark.sql(f"""
        INSERT INTO vinny_vijeyakumaar.stackoverflow_train01 VALUES
          ({x}, DATE("2007-08-01"), "", {x}, "", "", "", "", "", "", "", "", "", "", ""),
          ({y}, DATE("2007-08-01"), "", {y}, "", "", "", "", "", "", "", "", "", "", "")
      """)
    elif scenario == 1:
      # print(f"Scenario {scenario}")
      spark.sql("""
        UPDATE vinny_vijeyakumaar.stackoverflow_train01 VALUES
        SET tag5 = NULL
        WHERE PostId IN (
          SELECT PostId 
          FROM vinny_vijeyakumaar.stackoverflow_train01 
          TABLESAMPLE (2 ROWS)
        )
      """)
    elif scenario == 2:
      # print(f"Scenario {scenario}")
      spark.sql("""
        DELETE FROM vinny_vijeyakumaar.stackoverflow_train01
        WHERE PostId IN (
          SELECT PostId 
          FROM vinny_vijeyakumaar.stackoverflow_train01 
          TABLESAMPLE (2 ROWS)
        )
      """)
      

generate_transactions(10)

In [0]:
display_log_files()

Displaying contents of /Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01//_delta_log/


path name size modificationTime dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/.s3-optimization-0 .s3-optimization-0 0 1664313233000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/.s3-optimization-1 .s3-optimization-1 0 1664313233000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/.s3-optimization-2 .s3-optimization-2 0 1664313233000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000000.crc 00000000000000000000.crc 3213 1664313233000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000000.json 00000000000000000000.json 2444853 1664313230000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000001.crc 00000000000000000001.crc 3213 1664313687000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000001.json 00000000000000000001.json 3211640 1664313685000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000002.checkpoint.parquet 00000000000000000002.checkpoint.parquet 1141119 1664313819000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000002.crc 00000000000000000002.crc 3212 1664313815000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000002.json 00000000000000000002.json 3391011 1664313813000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000003.crc 00000000000000000003.crc 3212 1664313926000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000003.json 00000000000000000003.json 2248 1664313922000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000004.crc 00000000000000000004.crc 3212 1664313994000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000004.json 00000000000000000004.json 896 1664313993000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000005.crc 00000000000000000005.crc 3213 1664314025000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000005.json 00000000000000000005.json 2231 1664314022000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000006.crc 00000000000000000006.crc 3213 1664314052000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/00000000000000000006.json 00000000000000000006.json 2882 1664314050000 dbfs:/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-ove

In [0]:
display("/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/_last_checkpoint/")

'/Users/vinny.vijeyakumaar@databricks.com/custom_demos/lakehouse/predict-closed-questions-on-stack-overflow/stackoverflow_train01/_delta_log/_last_checkpoint/'

##![](https://pages.databricks.com/rs/094-YMS-629/images/delta-lake-tiny-logo.png) Schema enforcement & constraints

In [0]:
%sql
INSERT INTO vinny_vijeyakumaar.stackoverflow_train01 VALUES
  ("abc", "2007-08-01", "", "", "", "", "", "", "", "", "", "", "", "", "", "", "extraColumn"),
  ("xyz", DATE("2007-08-01"), "", 999999, "", "", "", "", "", "", "", "", "", "", "", "")

---------------------------------------------------------------------------
AnalysisException                         Traceback (most recent call last)
<command-4313537760280749> in <cell line: 1>()
      5     display(df)
      6     return df
----> 7   _sqldf = ____databricks_percent_sql()
      8 finally:
      9   del ____databricks_percent_sql

<command-4313537760280749> in ____databricks_percent_sql()
      2   def ____databricks_percent_sql():
      3     import base64
----> 4     df = spark.sql(base64.standard_b64decode("SU5TRVJUIElOVE8gdmlubnlfdmlqZXlha3VtYWFyLnN0YWNrb3ZlcmZsb3dfdHJhaW4wMSBWQUxVRVMKICAoImFiYyIsICIyMDA3LTA4LTAxIiwgIiIsICIiLCAiIiwgIiIsICIiLCAiIiwgIiIsICIiLCAiIiwgIiIsICIiLCAiIiwgIiIsICIiLCAiZXh0cmFDb2x1bW4iKSwKICAoInh5eiIsIERBVEUoIjIwMDctMDgtMDEiKSwgIiIsIDk5OTk5OSwgIiIsICIiLCAiIiwgIiIsICIiLCAiIiwgIiIsICIiLCAiIiwgIiIsICIiLCAiIik=").decode())
      5     display(df)
      6     return df

/databricks/spark/python/pyspark/instrumentation_utils.py in wrapper(*args, *

In [0]:
%sql
INSERT INTO vinny_vijeyakumaar.stackoverflow_train01 VALUES
  ("abc", "2007-08-01", "", "", "", "", "", "", "", "", "", "", "", "", "", ""),
  ("xyz", DATE("2007-08-01"), "", 999999, "", "", "", "", "", "", "", "", "", "", "", "")

---------------------------------------------------------------------------
AnalysisException                         Traceback (most recent call last)
<command-4313537760574787> in <cell line: 1>()
      5     display(df)
      6     return df
----> 7   _sqldf = ____databricks_percent_sql()
      8 finally:
      9   del ____databricks_percent_sql

<command-4313537760574787> in ____databricks_percent_sql()
      2   def ____databricks_percent_sql():
      3     import base64
----> 4     df = spark.sql(base64.standard_b64decode("SU5TRVJUIElOVE8gdmlubnlfdmlqZXlha3VtYWFyLnN0YWNrb3ZlcmZsb3dfdHJhaW4wMSBWQUxVRVMKICAoImFiYyIsICIyMDA3LTA4LTAxIiwgIiIsICIiLCAiIiwgIiIsICIiLCAiIiwgIiIsICIiLCAiIiwgIiIsICIiLCAiIiwgIiIsICIiKSwKICAoInh5eiIsIERBVEUoIjIwMDctMDgtMDEiKSwgIiIsIDk5OTk5OSwgIiIsICIiLCAiIiwgIiIsICIiLCAiIiwgIiIsICIiLCAiIiwgIiIsICIiLCAiIik=").decode())
      5     display(df)
      6     return df

/databricks/spark/python/pyspark/instrumentation_utils.py in wrapper(*args, **kwargs)
     46    

In [0]:
%sql
ALTER TABLE vinny_vijeyakumaar.stackoverflow_train01 
  ADD CONSTRAINT post_id_not_null CHECK (PostId IS NOT NULL);

ALTER TABLE vinny_vijeyakumaar.stackoverflow_train01 
  ADD CONSTRAINT post_creation_date_valid CHECK (
    PostCreationDate BETWEEN "2007-08-01" AND "2012-09-01");

---------------------------------------------------------------------------
AnalysisException                         Traceback (most recent call last)
<command-3008062229322502> in <cell line: 1>()
      6     display(df)
      7     return df
----> 8   _sqldf = ____databricks_percent_sql()
      9 finally:
     10   del ____databricks_percent_sql

<command-3008062229322502> in ____databricks_percent_sql()
      3     import base64
      4     spark.sql(base64.standard_b64decode("QUxURVIgVEFCTEUgdmlubnlfdmlqZXlha3VtYWFyLnN0YWNrb3ZlcmZsb3dfdHJhaW4wMSAKICBBREQgQ09OU1RSQUlOVCBwb3N0X2lkX25vdF9udWxsIENIRUNLIChQb3N0SWQgSVMgTk9UIE5VTEwp").decode())
----> 5     df = spark.sql(base64.standard_b64decode("QUxURVIgVEFCTEUgdmlubnlfdmlqZXlha3VtYWFyLnN0YWNrb3ZlcmZsb3dfdHJhaW4wMSAKICBBREQgQ09OU1RSQUlOVCBwb3N0X2NyZWF0aW9uX2RhdGVfdmFsaWQgQ0hFQ0sgKAogICAgUG9zdENyZWF0aW9uRGF0ZSBCRVRXRUVOICIyMDA3LTA4LTAxIiBBTkQgIjIwMTItMDktMDEiKQ==").decode())
      6     display(df)
      7     return df

/databricks/spa

In [0]:
%sql
DELETE FROM vinny_vijeyakumaar.stackoverflow_train01 
WHERE
  PostCreationDate < "2007-08-01"
  OR PostCreationDate > "2012-09-01"
  OR PostCreationDate IS NULL;
  
ALTER TABLE vinny_vijeyakumaar.stackoverflow_train01 
  ADD CONSTRAINT post_creation_date_valid CHECK (
    PostCreationDate BETWEEN "2007-08-01" AND "2012-09-01");

In [0]:
%sql
INSERT INTO vinny_vijeyakumaar.stackoverflow_train01 VALUES
  ("xyz", DATE("2022-09-29"), "", 999999, "", "", "", "", "", "", "", "", "", "", "")

---------------------------------------------------------------------------
Py4JJavaError                             Traceback (most recent call last)
<command-4313537760280750> in <cell line: 1>()
      5     display(df)
      6     return df
----> 7   _sqldf = ____databricks_percent_sql()
      8 finally:
      9   del ____databricks_percent_sql

<command-4313537760280750> in ____databricks_percent_sql()
      2   def ____databricks_percent_sql():
      3     import base64
----> 4     df = spark.sql(base64.standard_b64decode("SU5TRVJUIElOVE8gdmlubnlfdmlqZXlha3VtYWFyLnN0YWNrb3ZlcmZsb3dfdHJhaW4wMSBWQUxVRVMKICAoInh5eiIsIERBVEUoIjIwMjItMDktMjkiKSwgIiIsIDk5OTk5OSwgIiIsICIiLCAiIiwgIiIsICIiLCAiIiwgIiIsICIiLCAiIiwgIiIsICIiKQ==").decode())
      5     display(df)
      6     return df

/databricks/spark/python/pyspark/instrumentation_utils.py in wrapper(*args, **kwargs)
     46             start = time.perf_counter()
     47             try:
---> 48                 res = func(*args, **kwargs

##![](https://pages.databricks.com/rs/094-YMS-629/images/delta-lake-tiny-logo.png) Schema Evolution
With the `mergeSchema` option, you can evolve your Delta Lake table schema

## ![](https://pages.databricks.com/rs/094-YMS-629/images/delta-lake-tiny-logo.png) Let's Travel back in Time!
Databricks Delta’s time travel capabilities simplify building data pipelines for the following use cases. 

* Audit Data Changes
* Reproduce experiments & reports
* Rollbacks

As you write into a Delta table or directory, every operation is automatically versioned.

You can query by:
1. Using a timestamp
1. Using a version number

using Python, Scala, and/or Scala syntax; for these examples we will use the SQL syntax.  

For more information, refer to [Introducing Delta Time Travel for Large Scale Data Lakes](https://databricks.com/blog/2019/02/04/introducing-delta-time-travel-for-large-scale-data-lakes.html)

### ![](https://pages.databricks.com/rs/094-YMS-629/images/delta-lake-tiny-logo.png) Review Delta Lake Table History
All the transactions for this table are stored within this table including the initial set of insertions, update, delete, merge, and inserts with schema modification

In [0]:
%sql
DESCRIBE HISTORY vinny_vijeyakumaar.stackoverflow_train01
LIMIT 10 -- get the last 10 operations only

version timestamp userId userName operation operationParameters job notebook clusterId readVersion isolationLevel isBlindAppend operationMetrics userMetadata engineInfo 21 2022-09-27T22:58:15.000+0000 5211215277230706 vinny.vijeyakumaar@databricks.com ADD CONSTRAINT Map(name -> post_creation_date_valid, expr -> PostCreationDate BETWEEN "2007-08-01" AND "2012-09-01") null List(3008062229322400) 0923-094955-git4n0b4 20 WriteSerializable false Map() null Databricks-Runtime/11.2.x-photon-scala2.12 20 2022-09-27T22:58:13.000+0000 5211215277230706 vinny.vijeyakumaar@databricks.com DELETE Map(predicate -> ["(((hive_metastore.vinny_vijeyakumaar.stackoverflow_train01.PostCreationDate < DATE '2007-08-01') OR (hive_metastore.vinny_vijeyakumaar.stackoverflow_train01.PostCreationDate > DATE '2012-09-01')) OR (hive_metastore.vinny_vijeyakumaar.stackoverflow_train01.PostCreationDate IS NULL))"]) null List(3008062229322400) 0923-094955-git4n0b4 19 WriteSerializable false Map(numRemovedFiles -> 1, numAddedChangeFiles -> 0, executionTimeMs -> 497, scanTimeMs -> 497, rewriteTimeMs -> 0) null Databricks-Runtime/11.2.x-photon-scala2.12 19 2022-09-27T21:39:55.000+0000 5211215277230706 vinny.vijeyakumaar@databricks.com DELETE Map(predicate -> ["((hive_metastore.vinny_vijeyakumaar.stackoverflow_train01.PostCreationDate < DATE '2007-08-01') OR (hive_metastore.vinny_vijeyakumaar.stackoverflow_train01.PostCreationDate > DATE '2012-09-01'))"]) null List(3008062229322400) 0923-094955-git4n0b4 18 WriteSerializable false Map(numRemovedFiles -> 1, numAddedChangeFiles -> 0, executionTimeMs -> 32, scanTimeMs -> 31, rewriteTimeMs -> 0) null Databricks-Runtime/11.2.x-photon-scala2.12 18 2022-09-27T21:34:23.000+0000 5211215277230706 vinny.vijeyakumaar@databricks.com WRITE Map(mode -> Append, partitionBy -> []) null List(3008062229322400) 0923-094955-git4n0b4 17 WriteSerializable true Map(numFiles -> 1, numOutputRows -> 1, numOutputBytes -> 2853) null Databricks-Runtime/11.2.x-photon-scala2.12 17 2022-09-27T21:34:19.000+0000 5211215277230706 vinny.vijeyakumaar@databricks.com ADD CONSTRAINT Map(name -> post_id_not_null, expr -> PostId IS NOT NULL) null List(3008062229322400) 0923-094955-git4n0b4 16 WriteSerializable false Map() null Databricks-Runtime/11.2.x-photon-scala2.12 16 2022-09-27T21:29:25.000+0000 5211215277230706 vinny.vijeyakumaar@databricks.com WRITE Map(mode -> Append, partitionBy -> []) null List(3008062229322400) 0923-094955-git4n0b4 15 WriteSerializable true Map(numFiles -> 1, numOutputRows -> 2, numOutputBytes -> 3228) null Databricks-Runtime/11.2.x-photon-scala2.12 15 2022-09-27T21:29:19.000+0000 5211215277230706 vinny.vijeyakumaar@databricks.com UPDATE Map(predicate -> PostId#23156 IN (list#23140 [])) null List(3008062229322400) 0923-094955-git4n0b4 14 WriteSerializable false Map(numRemovedFiles -> 1, numCopiedRows -> 30, numAddedChangeFiles -> 1, executionTimeMs -> 5014, scanTimeMs -> 3688, numAddedFiles -> 1, numUpdatedRows -> 2, rewriteTimeMs -> 1287) null Databricks-Runtime/11.2.x-photon-scala2.12 14 2022-09-27T21:29:12.000+0000 5211215277230706 vinny.vijeyakumaar@databricks.com WRITE Map(mode -> Append, partitionBy -> []) null List(3008062229322400) 0923-094955-git4n0b4 13 WriteSerializable true Map(numFiles -> 1, numOutputRows -> 2, numOutputBytes -> 3228) null Databricks-Runtime/11.2.x-photon-scala2.12 13 2022-09-27T21:29:10.000+0000 5211215277230706 vinny.vijeyakumaar@databricks.com WRITE Map(mode -> Append, partitionBy -> []) null List(3008062229322400) 0923-094955-git4n0b4 12 WriteSerializable true Map(numFiles -> 1, numOutputRows -> 2, numOutputBytes -> 3228) null Databricks-Runtime/11.2.x-photon-scala2.12 12 2022-09-27T21:29:08.000+0000 5211215277230706 vinny.vijeyakumaar@databricks.com WRITE Map(mode -> Append, partitionBy -> []) null List(3008062229322400) 0923-094955-git4n0b4 11 WriteSerializable true Map(numFiles -> 1, numOutputRows -> 2, numOutputBytes -> 3228) null Databricks-Runtime/11.2.x-photon-scala2.12

### ![](https://pages.databricks.com/rs/094-YMS-629/images/delta-lake-tiny-logo.png) Time Travel via Version Number or Timestamp
Below are SQL syntax examples of Delta Time Travel by using a **version number** or **timestamp**

In [0]:
%sql
WITH rec_count_00 AS (
  SELECT COUNT(*) AS n FROM vinny_vijeyakumaar.stackoverflow_train01 
  VERSION AS OF 1
)
, rec_count_01 AS (
  SELECT COUNT(*) AS n FROM vinny_vijeyakumaar.stackoverflow_train01
  TIMESTAMP AS OF (CURRENT_TIMESTAMP() - INTERVAL 40 MINUTES)
)
, rec_count_now AS (
  SELECT COUNT(*) AS n FROM vinny_vijeyakumaar.stackoverflow_train01
  VERSION AS OF 21
)
SELECT r0.n AS start, r1.n AS 40MinsAgo, rn.n AS now
FROM rec_count_00 r0, rec_count_01 r1, rec_count_now rn

start 40MinsAgo now 3352998 3353020 3353016

### ![](https://pages.databricks.com/rs/094-YMS-629/images/delta-lake-tiny-logo.png) Restoring previous versions of a Delta Table

[Documentation](https://docs.delta.io/latest/delta-utility.html#restore-a-delta-table-to-an-earlier-state)

In [0]:
%sql
-- Restore table to previous state
RESTORE TABLE vinny_vijeyakumaar.stackoverflow_train01 
TO VERSION AS OF 12 -- by version
-- TO TIMESTAMP AS OF "2022-09-28 10:00:00" -- or by point in time

-sandbox
## ![](https://pages.databricks.com/rs/094-YMS-629/images/delta-lake-tiny-logo.png) Delta Lake CDF (Change Data Feed) to support data sharing and Datamesh organization
<img src="https://github.com/QuentinAmbard/databricks-demo/raw/main/retail/resources/images/delta-cdf-datamesh.png" style="float:right; margin-right: 50px" width="300px" />
&nbsp;

Enable [Change Data Feed](https://docs.delta.io/2.0.0/delta-change-data-feed.html) on your Delta table. With CDF, you can track all the changes (INSERT/UPDATE/DELETE) from your table.

It's then easy to subscribe to modifications stream on one of your table to propagate changes downsteram (e.g. GDPR DELETEs downstream)

### Enable Change Data Feed on an existing table
If you wish to enable Change Data Feed on an existing table, simply alter the table's `TBLPROPERTIES`

In [0]:
%sql
ALTER TABLE vinny_vijeyakumaar.stackoverflow_train01
SET TBLPROPERTIES (delta.enableChangeDataFeed = true)

### View changes to the table
Query the metatable `TABLE_CHANGES` to view change data history.

In [0]:
%sql
SELECT * FROM TABLE_CHANGES("vinny_vijeyakumaar.stackoverflow_train01", 0)
WHERE PostId = "1167904"

PostId PostCreationDate OwnerUserId OwnerCreationDate ReputationAtPostCreation OwnerUndeletedAnswerCountAtPostTime Title BodyMarkdown Tag1 Tag2 Tag3 Tag4 Tag5 PostClosedDate OpenStatus _change_type _commit_version _commit_timestamp 1167904 2007-08-01 1167904 update_postimage 6 2022-09-27T21:27:30.000+0000 1167904 2007-08-01 1167904 update_preimage 6 2022-09-27T21:27:30.000+0000 1167904 2007-08-01 1167904 insert 5 2022-09-27T21:27:02.000+0000

### Propagate changes downstream
This is just an example. Attempting to run it won't work unless you have the relevant target table already created.

In [0]:
%sql
INSERT INTO target_schema.target_table 
SELECT * EXCEPT (_change_type, _commit_version, _commit_timestamp)
-- Let's assume our orchestration tool knows that the last update happened at 2022-09-29 00:00:00
FROM TABLE_CHANGES("vinny_vijeyakumaar.stackoverflow_train01", "2022-09-29 00:00:00")
WHERE _change_type IN ("insert", "update_postimage");


DELETE FROM target_schema.target_table 
WHERE PostId IN (
  SELECT PostId
  -- Let's assume our orchestration tool knows that the last update happened at 2022-09-29 00:00:00
  FROM TABLE_CHANGES("vinny_vijeyakumaar.stackoverflow_train01", "2022-09-29 00:00:00")
  WHERE _change_type IN ("delete")
);